In [1]:
pip install ipwhois

Note: you may need to restart the kernel to use updated packages.


In [2]:
import pandas as pd
import numpy as np
from ipwhois import IPWhois

# Header for the imported traffic logs (there is an additional column for some reason..? :/)
traffic_log = ['Type', 'sflow_agent_address', 'inputPort', 'outputPort',
               'src_MAC', 'dst_MAC', 'ethernet_type', 'in_vlan', 'out_vlan',
               'src_IP', 'dst_IP', 'IP_protocol', 'ip_tos', 'ip_ttl',
               'src_transport_port', 'dst_transport_port', 'tcp_flags',
               'packet_size', 'IP_size', 'sampling_rate', '???']

In [3]:
log_df = pd.read_csv('SFlow_Data_lab4.csv', header=None, names=traffic_log)
log_df.drop('???', axis=1, inplace=True)   # dropping the additional column full of null values
log_df.head(10)

Type sflow_agent_address  inputPort  outputPort       src_MAC  \
0  FLOW         aa.aa.aa.aa        137         200  d404ff55fd4d   
1  FLOW         aa.aa.aa.aa        129         193  609c9f851b00   
2  FLOW         aa.aa.aa.aa        137         200  d404ff55fd4d   
3  FLOW         aa.aa.aa.aa        129         135  609c9f851b00   
4  FLOW         aa.aa.aa.aa        130         199  00239cd087c1   
5  FLOW         aa.aa.aa.aa        129         135  609c9f851b00   
6  FLOW         aa.aa.aa.aa        130         199  00239cd087c1   
7  FLOW         aa.aa.aa.aa        137         200  d404ff55fd4d   
8  FLOW         aa.aa.aa.aa        200           3  80711fc76001   
9  FLOW         aa.aa.aa.aa        199         130  544b8cf9a7df   

        dst_MAC ethernet_type  in_vlan  out_vlan          src_IP  \
0  80711fc76001        0x0800    919.0       280  130.246.176.22   
1  0031466b23cf        0x0800     11.0       919   155.69.160.32   
2  80711fc76001        0x0800    919.0       280  130.246.176.53   
3  002688cd5fc7        0x0800     11.0       919   155.69.160.32   
4  544b8cf9a7df        0x0800    919.0       600  137.132.228.15   
5  002688cd5fc7        0x0800     11.0       919   155.69.160.32   
6  544b8cf9a7df        0x0800    919.0       600   137.132.250.8   
7  80711fc76001        0x0800    919.0       280  193.61.196.206   
8  00235ed9b680        0x0800    280.0        32  137.189.133.62   
9  00239cd087c1        0x0800    600.0       919    193.62.192.8   

            dst_IP  IP_protocol ip_tos  ip_ttl  src_transport_port  \
0    140.115.32.81            6   0x00      50             51216.0   
1   64.233.188.128            6   0x00      56             23159.0   
2    140.115.32.83            6   0x00      50             50041.0   
3    54.169.174.79           17   0x00     120             54241.0   
4     193.62.192.8            6   0x00      56             53923.0   
5   54.255.221.151           17   0x00     120             55069.0   
6     193.62.193.9            6   0x00      62             27419.0   
7  140.110.147.170            6   0x00     240               443.0   
8     123.136.64.7            6   0x00      58              6345.0   
9   137.132.228.15            6   0x08      55             34262.0   

   dst_transport_port tcp_flags  packet_size  IP_size  sampling_rate  
0               23505      0x10         1518     1500           2048  
1                  80      0x10           74       52           2048  
2               20739      0x10         1518     1500           2048  
3               26510      0x10          116       94           2048  
4               34262      0x10           70       52           2048  
5               26509      0x10          113       91           2048  
6                  80      0x10           58       40           2048  
7               43545      0x18         1518     1500           2048  
8               34921      0x10         1342     1320           2048  
9               53923      0x10         1442     1420           2048

# 4A: Top talkers and listeners

In [4]:
# function to find the organisation name given the IP address
def find_org(ip_addr):
    ip = IPWhois(ip_addr)
    result = ip.lookup_rdap()
    return result.get('network', {}).get('name')

## Find Top 5 Talkers (sender nodes)

In [5]:
# get the top 5 unique IP addresses by no. of packets sent (each entry in the log is 1 packet)
top_senders = log_df['src_IP'].value_counts().nlargest(5).to_frame()
org = []

# Identify the organisations
for ip_addr in top_senders.index:
    org.append(find_org(ip_addr))
    
top_senders['Organisation'] = org    # append org. data to the dataframe

In [6]:
top_senders = top_senders.reset_index().rename(columns={'index':'IP address', 'src_IP':'# of packets'})
top_senders

IP address  # of packets      Organisation
0   193.62.192.8          3041      EUR-BIO-INST
1  155.69.160.32          2975           NTUNET1
2  130.14.250.11          2604         NLM-ETHER
3  14.139.196.58          2452       NKN-IIT-GUW
4  140.112.8.139          2056  T-NTU.EDU.TW-NET

## Find Top 5 Listeners (receiving nodes)

In [7]:
# get the top 5 unique IP addresses by no. of packets received (each entry in the log is 1 packet)
top_receivers = log_df['dst_IP'].value_counts().nlargest(5).to_frame()
org = []

# Identify the organisations
for ip_addr in top_receivers.index:
    org.append(find_org(ip_addr))
    
top_receivers['Organisation'] = org    # append org. data to the dataframe

In [8]:
top_receivers = top_receivers.reset_index().rename(columns={'index':'IP address', 'dst_IP':'# of packets'})
top_receivers

IP address  # of packets  Organisation
0   103.37.198.100          3841  A-STAR-AS-AP
1   137.132.228.15          3715        NUSNET
2   202.21.159.244          2446         RPNET
3  192.101.107.153          2368          PNNL
4     103.21.126.2          2056       IITB-IN

# 4B:  Transport protocol

## Find Proportion of TCP and UDP packets

In [9]:
packet_df = log_df['IP_protocol'].value_counts().to_frame()
packet_df = packet_df.reset_index().rename(columns={'index' : 'Header value', 'IP_protocol' : '# of packets'})

In [10]:
percent_total = []
for i in range(len(packet_df)):
    percent_total.append(packet_df['# of packets'][i] * 100 / len(log_df))

packet_df['% total'] = percent_total
packet_df

Header value  # of packets    % total
0             6         56064  80.818798
1            17          9462  13.639902
2            50          1698   2.447744
3             0          1261   1.817789
4            47           657   0.947095
5            41           104   0.149921
6             1            74   0.106674
7           381            45   0.064870
8            58             4   0.005766
9           103             1   0.001442

In [11]:
# Finding specifically TCP and UDP packet data
# TCP = 6
# UDP = 17
tcp_packet_df = packet_df.loc[packet_df['Header value'] == 6]
udp_packet_df = packet_df.loc[packet_df['Header value'] == 17]
frames = [tcp_packet_df, udp_packet_df]
final_df = pd.concat(frames)
final_df

Header value  # of packets    % total
0             6         56064  80.818798
1            17          9462  13.639902

# 4C: Applications protocol

## Find Top 5 Applications
Used https://www.adminsub.net/tcp-udp-port-finder to find the service

In [12]:
dest_port_df = log_df['dst_transport_port'].value_counts().nlargest(5).to_frame()
dest_port_df = dest_port_df.reset_index().rename(columns={'index':'Destination IP port number', 'dst_transport_port':'# of packets'})

In [13]:
# Mapping of services (hard-coded)
app_port_map = {45512: 'Unassigned', 443: 'HTTPS', 80: 'HTTP', 52866: 'Dynamic and/or Private Ports', 56152: 'Dynamic and/or Private Ports', 0: 'Reserved port (not used for TCP/UDP)'}
service = []
for i in dest_port_df['Destination IP port number']:
    try:
        service.append(app_port_map[i])
    except:
        service.append('Unknown')
dest_port_df['Service'] = service

In [14]:
dest_port_df

Destination IP port number  # of packets                       Service
0                         443         13423                         HTTPS
1                          80          2647                          HTTP
2                       52866          2068  Dynamic and/or Private Ports
3                       45512          1356                    Unassigned
4                       56152          1341  Dynamic and/or Private Ports

# 4D: Traffic

## Find Total Traffic
Use IP packet size --> IP_size in log_df

In [15]:
total_traffic = sum(log_df['IP_size'])
# Assuming that IP_size is given in terms of bits
total_traffic_Mb = total_traffic / (8 * pow(2, 20))
print(f"Total traffic(Mb) = {total_traffic_Mb:.3f} Mb")

Total traffic(Mb) = 7.722 Mb


# 4E: Additional analysis

In [16]:
# Find all unique communication pairs
comm_pairs_df = log_df.groupby(['src_IP', 'dst_IP']).size().sort_values(ascending=False).to_frame()
comm_pairs_df.columns=['# of packets']
comm_pairs_df = comm_pairs_df.reset_index()
comm_pairs_df

src_IP  \
0                                193.62.192.8   
1                               130.14.250.11   
2                               14.139.196.58   
3                               140.112.8.139   
4                              137.132.228.15   
...                                       ...   
6584                            155.69.193.14   
6585                           155.69.193.139   
6586                           155.69.193.115   
6587                           155.69.193.112   
6588  fe80:0000:0000:0000:b2a8:6e03:ca76:6716   

                                       dst_IP  # of packets  
0                              137.132.228.15          3041  
1                              103.37.198.100          2599  
2                             192.101.107.153          2368  
3                                103.21.126.2          2056  
4                                193.62.192.8          1910  
...                                       ...           ...  
6584                             172.217.27.1             1  
6585                             172.217.27.3             1  
6586                           74.125.130.188             1  
6587                             74.125.68.95             1  
6588  fe80:0000:0000:0000:ce4e:24ff:fe9c:6314             1  

[6589 rows x 3 columns]

## Find Top 5 Communication pair
Doing so based on the top 5 {source, destination} pairs

In [17]:
# Get top 5 comm pairs
top_comm_df = comm_pairs_df[:5]

src_org = []
dst_org = []

for i in range(5):
    src_org.append(find_org(top_comm_df['src_IP'][i]))
    dst_org.append(find_org(top_comm_df['dst_IP'][i]))
    
top_comm_df['Source Organisation'] = src_org
top_comm_df['Destination Organisation'] = dst_org

C:\Users\h34v3\AppData\Local\Temp/ipykernel_25532/3655958046.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_comm_df['Source Organisation'] = src_org
C:\Users\h34v3\AppData\Local\Temp/ipykernel_25532/3655958046.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  top_comm_df['Destination Organisation'] = dst_org


In [18]:
top_comm_df = top_comm_df.reindex(['src_IP', 'Source Organisation', 'dst_IP', 'Destination Organisation', '# of packets'], axis = 'columns')
top_comm_df

src_IP Source Organisation           dst_IP  \
0    193.62.192.8        EUR-BIO-INST   137.132.228.15   
1   130.14.250.11           NLM-ETHER   103.37.198.100   
2   14.139.196.58         NKN-IIT-GUW  192.101.107.153   
3   140.112.8.139    T-NTU.EDU.TW-NET     103.21.126.2   
4  137.132.228.15              NUSNET     193.62.192.8   

  Destination Organisation  # of packets  
0                   NUSNET          3041  
1             A-STAR-AS-AP          2599  
2                     PNNL          2368  
3                  IITB-IN          2056  
4             EUR-BIO-INST          1910

## Visualise communication between different IP hosts

In [19]:
import networkx as nx
import matplotlib.pyplot as plt

In [20]:
# get all IP addresses that were source addresses
srcIP = comm_pairs_df['src_IP']
# get all IP addresses that were destination addresses
dstIP = comm_pairs_df['dst_IP']

In [21]:
G = nx.Graph()
# edges and nodes are defined as set() to avoid repeated values
edges = set()
nodes = set()

for i in range(len(comm_pairs_df)):
    sIP = srcIP[i]
    dIP = dstIP[i]
    nodes.add(sIP)
    nodes.add(dIP)
    edges.add((sIP,dIP))

In [22]:
G.add_nodes_from(nodes)
G.add_edges_from(edges)
plt.rcParams['figure.figsize'] = 150,120
p = nx.spring_layout(G,scale = 1.0, iterations = 50)

f=plt.figure()
nx.draw(G,p,ax=f.add_subplot(111),node_color = 'r',edge_color = 'g', with_labels = True)